# MTF053 - Computer Assignment 1 (CA1) - Numerical Analysis of Fully Develooped Channel Flow

In this exercise, you will study a fully developed channel flow (flow between two parallel plates) numerically. You will start with a laminar flow as that problem can be solved analytically and thus it is possible to make a comparison and get a feeling for the accuracy of the numerical method. In the second part of the assignment, you will analyze a turbulent flow numerically and compare your results to provided measured data. The numerical part will be done using `Python` codes provided below. You will need to make some minor modifications to some of the codes. In the header of each code segment, there is a description of what modifications that should be done if any. 

The assignemnt is divided into tasks some of which includes running numerical simulations. You can run the python codes directly in this `Jupyter NoteBook`. For some of the tasks, you are expected to write down answers to questions. This should be done in the dedicated sections in this notebook titled *"answer to task x.y"*.

More detailed instructions, theory and background are given in the assignment instruction document [MTF053_CA1.pdf](https://courses.onlineflowcalculator.com/fluidmech/docs/MTF053_CA1.pdf).

## Jupyter notebook instructions

### Edit a notebook cell

Double click on the cell to enter edit mode. 

### Update a cell

With the cell marked, klick on the play symbol in at the top of the notebook

### Add a new cell

Click on the cell above or below which you want a new cell and click on one of the symbols at the top right corner of the marked cell. Set cell type (Markdown or Code) for the new cell by clicking the cell and select *Code* or *Markdown* in the dropdown list in the top menu of the notebook. You'll find a good documentation of Markdown [here](https://www.markdownguide.org/basic-syntax/).

### Add an image in a Markdown cell

If you like to include an image in one of the Markdown text cells (for example if you want to include a photo of a derivation made on paper), do as follows:

1. upload your image using the *upload files* function

2. include the image in the notebook by writing: \!\[title\]\(image.png\)

3. typeset the cell by klicking the play icon at the top of the notebook to see the result

You can also include an image available online, add Markdown code as follows: \!\[title\]\(url\)

If it does not work to include a local image in a Markdown cell, add a new code cell and add the following code

`Image(filename='filename.jpg')`


---
# Initialization
---
Make sure to execute the code section below before runnig any of the other code sections that follows as this will load the `python` libraries needed.

In [10]:
#********************************************************
#
# NO NEED FOR MODIFICATIONS IN THIS NOTEBOOK SECTION
#
#********************************************************

# IMPORT THE PYTHON LIBRARIES NEEDED 

import numpy as np
from scipy.sparse import diags
from scipy.sparse.linalg import spsolve
import matplotlib.pyplot as plt
from IPython.display import Image

# DEFINITION OF GLOBAL VARIABLES

verbose  = 0    # verbose solver output activated if verbose=1 
FontSize = 20

# geometry

h     =  0.06   # channel height

# fluid properties

mu    =  1.8e-5 # fluid viscosity (dynamic viscosity)
rho   =  1.2    # fluid density

# log-law constants

kappa =  0.41   # von Kármán constant
B     =  5.0    # integration constant in the log-law


# DEFINITION OF HELP FUNCTIONS

#========================================================
# mesh generation for laminar channel flow
#========================================================
def generate_mesh_for_laminar_flow_simulation(N,h):
    
    # allocate y vector
    
    y = np.zeros(N+2)
    
    # calculate cell size (dy) assuming equidistant grid

    dy=(h/2.0)/N  
    
    # add wall-normal coordinates for all cells (cell 1 to N) 

    y[slice(1,N+1)] = np.linspace(dy/2.0,0.5*h-(dy/2.0),N)

    # add centerline coordinate

    y[-1]=h/2. 
    
    return y

#========================================================
# get an estimate of the numerical error
# for a laminar channel flow simulation 
# (diff from analytic)
#========================================================
def laminar_flow_calculate_error(U,Ua):
    
    if Ua[-2] == 0.0 :
        return -1
    
    # calcualte relative error (deviation in last cell)
    
    return np.abs((U[-2]-Ua[-2])/Ua[-2])

#========================================================
# calculate max velocity (laminar channel flow)
#========================================================
def laminar_flow_get_umax(h,dpdx,mu):
    
    # calculate the analytic maximum velocity (channel center)
    
    return -0.125*h**2*dpdx/mu

#========================================================
# calculate y+ and u+ from y, U, tau_w, rho, and mu
#========================================================
def calc_yplus_uplus(rho,mu,tau_w,y,U):
    nu=mu/rho
    ustar=np.sqrt(tau_w/rho)
    yplus=y*ustar/nu
    uplus=U/ustar
    return yplus,uplus


# 1. Laminar Channel Flow

---
## Task 1.1
---

Show that the Navier-Stokes equations

$$\dfrac{\partial u}{\partial x}+\dfrac{\partial v}{\partial y}=0$$

$$\rho\left(u\dfrac{\partial u}{\partial x}+v\dfrac{\partial u}{\partial y}\right)=-\dfrac{\partial p}{\partial x}+\rho g_x+\dfrac{\partial}{\partial x}\left(\mu\dfrac{\partial u}{\partial x}\right)+\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial u}{\partial y}\right)$$

$$\rho\left(u\dfrac{\partial v}{\partial x}+v\dfrac{\partial v}{\partial y}\right)=-\dfrac{\partial p}{\partial y}+\rho g_y+\dfrac{\partial}{\partial x}\left(\mu\dfrac{\partial v}{\partial x}\right)+\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial v}{\partial y}\right)$$

reduces to

$$\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial u}{\partial y}\right) = \dfrac{\partial p}{\partial x}$$

for fully developed laminar channel flow in two dimensions. Examining the equation above, it is obvious that for our specified application, it is possible to reduce the number of terms in the Navier-Stokes equations significantly, which means that you will remove terms in the equations as part of the derivations. Please note, however, that all such modifications of the equations must be justified.


**Hint:** the lecture notes for chapter 4 ([MTF053_C04.pdf](https://courses.onlineflowcalculator.com/fluidmech/notes/MTF053_C04.pdf)) may be of use here.

### Answer to task 1.1

<font color="red">**write down your answer here**</font>

**Note!** derivations made uisng pen and paper or a tablet can be included as photos/images. Upload the photo or image and include as described at the top of this document.


---
## Task 1.2
---

1. Solve the simplified equation from task 1.1 analytically for the above-listed boundary conditions and flow properties
2. Calculate the Reynolds number

Remember that we are investigating the flow in a two-dimensional channel, i.e., it is **not** a pipe flow. The correct hydraulic diameter for such a *non-circular pipe flow* can be found in [MTF053_Formulas-Tables-and-Graphs.pdf](https://courses.onlineflowcalculator.com/fluidmech/docs/MTF053_Formulas-Tables-and-Graphs.pdf). Also, the Reynolds number should be calculated using the average velocity, which can be obtained by integrating over the channel

$$V=\dfrac{1}{h}\int_0^hu(y)dy$$


### Answer to task 1.2

<font color="red">**write down your answers here**</font>

**Note!** derivations made uisng pen and paper or a tablet can be included as photos/images. Upload the photo or image and include as described at the top of this document.

---
## Task 1.3
---

Write the equation system that we get by evaluating 

$$u_{i+1}-2u_{i}+u_{i-1}=\dfrac{\partial p}{\partial x}\dfrac{\Delta y^2}{\mu}$$

in all of the $N$ cells on matrix form, i.e., write the equation above as $A\mathbf{u}=\mathbf{b}$, where $\mathbf{u}$ is a vector with $N$ elements. What does the matrix $A$ and the vector $\mathbf{b}$ look like?

To solve this rather simple problem, all we have to do now is to invert the matrix $A$ and then the velocity values are calculated as $\mathbf{u}=A^{-1}\mathbf{b}$

### Answers to task 1.3

<font color="red">**write down your answers here**</font>

**Note!** derivations made uisng pen and paper or a tablet can be included as photos/images. Upload the photo or image and include as described at the top of this document.


---
## Task 1.4
---

Below you'll find a `Python` code that solves the equation system derived in Task 1.3 using the `Python` functions `scipy.sparse.diags` and `scipy.sparse.linalg.spsolve`.

Before running the solver, you must make some minor changes in the codes:

1. in the function `laminar_channel_flow_solver`, specify the boundary entries in the coefficient matrix $A$
2. in the function `get_analytic_laminar_velocity_profile`, implement calculation of analytical solution for laminar channel flow
3. in the main code for task 1.4, specify number of cells

With these changes made it is now time to run the code. To execute the code in a code cell, click on the code cell to make it active and then click on the play button at the top of the notebook. Make sure to execute the code cells in sequence. The functions `laminar_channel_flow_solver` and `get_analytic_laminar_velocity_profile` must be executed before running the task 1.4 main code.


### Laminar flow solver
Below you find a template for a laminar flow solver written in `python`. Before running the solver you will have to make a few minor changes (indicated in the code)

In [11]:

# FUNCTION: laminar_channel_flow_solver(y,mu,rho,dpdx)

#********************************************************
#
# CODE MODIFICATION NEEDED: 
#
# 1. IMPLEMENT BOUNDARY CONDITIONS
#
#********************************************************

#========================================================
# laminar channel flow solver
# numerical calculation of a laminar boundary layer 
# velocity profile using a finite-volume approach
#========================================================
#
#      0     1     2            N-1    N    N+1
#   ------------------- - - - -------------------
#   |     |     |     |       |     |     |     |
#   |  o  |  o  |  o  |       |  o  |  o  |  o  |
#   | G1  |     |     |       |     |     | G2  |
#   ------------------- - - - -------------------
#         ^                               ^      
#      	 y=0.                           y=h/2    
#        u=0.                          du/dy=0
#
# The computational domain contains N cells ranging 
# from cell 1 to cell N. G1 and G2 are ghost cells 
# (cells outside of the computational domain used for
# boundary condition implementation).
#========================================================

def laminar_channel_flow_solver(y,mu,rho,dpdx):
    
    N = len(y) - 2
    
    dy=2.0*(y[1]-y[0])
    
    # allocate U vector
    
    U = np.zeros(N+2)

    # generate matrix diagonal vector and off-diagonal vectors

    diagonal  = -2.0*np.ones(N)
    off_diagonal = np.ones(N-1)

    # set boundary conditions (update diagonal elements)

    diagonal[ 0] = 0 # <= ADD LEFT-END BOUNDARY CONDITION HERE
    diagonal[-1] = 0 # <= ADD RIGHT-END BOUNDARY CONDITION HERE
    
    if diagonal[0] == 0 and diagonal[-1] == 0 :
        return U

    # generate sparse matrix (A) (note! the sparse library functions 
    # are used in order to make the code more efficient)

    A = diags([diagonal,off_diagonal,off_diagonal],[0, -1, 1],format="csr")

    # generate right-hand-side vector (b)

    b = (dpdx*dy**2/mu)*np.ones(N)

    # solve linear equation system AU=b => U=inv(A)b

    U[slice(1,N+1)] = spsolve(A,b)

    # update boundary velocity

    U[-1] = U[-2]
    
    return U


### Running the laminar flow solver
Here you define variables necessary to run the laminar flow solver. Make sure to run the code above first since the function defined there will be used in the code below.

In [12]:

# FUNCTION: get_analytic_laminar_velocity_profile(y,h,dpdx,mu)

#********************************************************
#
# CODE MODIFICATION NEEDED: 
#
# 1. CALCULATE ANALYTIC SOLUTION (LAMINAR CHANNEL FLOW)
#
#********************************************************

#========================================================
# function that calculates the analytic solution for 
# laminar channel flow
#========================================================
def get_analytic_laminar_velocity_profile(y,h,dpdx,mu):
    
    # calculate the velocity for all y-coordinates (analytic solution)
    
    Ua = y*0.0 # <= CALCULATE ANALYTIC SOLUTION HERE U(y)
    
    return Ua


In [13]:

# TASK 1.4 main code

#********************************************************
#
# CODE MODIFICATION NEEDED: 
#
# 1. SPECIFY CELL COUNT
#
#********************************************************

#========================================================
# running the laminar channel flow solver
#========================================================

dpdx  = -0.01   # pressure gradient
N     =  0      # number of cells  <= SET CELL COUNT HERE

if N > 0 :
    
    # generate mesh

    y_lam = generate_mesh_for_laminar_flow_simulation(N,h)

    # run laminar channel flow solver 

    U_lam = laminar_channel_flow_solver(y_lam,mu,rho,dpdx)

    # calculate analytic solution (laminar flow)

    U_analytic = get_analytic_laminar_velocity_profile(y_lam,h,dpdx,mu) 

    # plot laminar flow velocity profile

    fig = plt.figure(num=1, figsize=(15, 10), dpi=80, facecolor='w', edgecolor='k')
    ax = fig.add_subplot(111)
    ax.plot(U_lam,y_lam,linewidth=2,label='numeric' )
    ax.plot(U_analytic,y_lam,linewidth=2,label='analytic')
    ax.set_xlabel('axial velocity (u [m/s])',fontsize=FontSize)
    ax.set_ylabel('wall-normal coordinate (y [m])',fontsize=FontSize)
    ax.set_title('Velocity profile - laminar channel flow',fontsize=FontSize)
    ax.legend(fontsize=FontSize)
    ax.set_xlim(0,round(laminar_flow_get_umax(h,dpdx,mu)*100)/100)
    ax.set_ylim(0,0.5*h)
    for label in (ax.get_xticklabels() + ax.get_yticklabels()):
        label.set_fontsize(FontSize)
    ax.grid()
    
    plt.show()


---
## Task 1.5
---

For this task, you'll find a `Python` code that runs the laminar flow solver set up in the previous task and calculates the error ($e$) according to

$$e=\left|\dfrac{u_{numeric}-u_{analytic}}{u_{analytic}}\right|$$

for 10 different values of $N$ (number of iterations) spanning from $N=10$ to $N=1000$. Note that the `Python` function `numpy.logspace` is used to distribute the cell counts. After running the laminar flow solver with 10 different cell counts and calculating the error for each case, a `loglog` plot showing the error as a function of cell count is generated.

1. How does the error decay with increased cell count?

    <font color="red">**write down your answer here**</font>
    
2. When calculating the error, why is $u_{analytic}$ not calculated at the center of the duct?

    <font color="red">**write down your answer here**</font>


In [5]:

# TASK 1.5 main code

#********************************************************
#
# NO CODE MODIFICATIONS NEEDED IN THIS NOTEBOOK SECTION
#
#********************************************************

# case-specific properties

dpdx  = -0.01   # pressure gradient

# generate a vector with cell counts spanning from 10 to 1000

NN = np.int_(np.logspace(1,3,10))

# allocate vectors

err        = []
y_lam      = []
U_lam      = []
U_analytic = []

# run the laminar flow solver for each cell count N in the array NN

for N in NN:
    
    # generate mesh

    y_lam = generate_mesh_for_laminar_flow_simulation(N,h)

    # run laminar channel flow solver 

    U_lam = laminar_channel_flow_solver(y_lam,mu,rho,dpdx)

    # get analytic solution (laminar flow)

    U_analytic = get_analytic_laminar_velocity_profile(y_lam,h,dpdx,mu)

    # calculate error
    
    error = laminar_flow_calculate_error(U_lam,U_analytic)

    # append error to the error array 
    
    err.append(error)
    
    
# plot velocity results

if err[0] > 0.0 :

    fig = plt.figure(num=1, figsize=(15, 10), dpi=80, facecolor='w', edgecolor='k')

    ax = fig.add_subplot(121)
    ax.plot(U_lam ,y_lam,linewidth=2,label='numeric' )
    ax.plot(U_analytic,y_lam,linewidth=2,label='analytic')
    ax.set_xlabel('axial velocity (u [m/s])',fontsize=FontSize)
    ax.set_ylabel('wall-normal coordinate (y [m])',fontsize=FontSize)
    ax.set_title('Velocity profile - laminar channel flow',fontsize=FontSize)
    ax.legend(fontsize=FontSize)
    ax.set_xlim(0,round(laminar_flow_get_umax(h,dpdx,mu)*100)/100)
    ax.set_ylim(0,0.5*h)
    for label in (ax.get_xticklabels() + ax.get_yticklabels()):
        label.set_fontsize(FontSize)
    ax.grid()

    ax = fig.add_subplot(122)
    ax.loglog(NN,err,'-o',linewidth=2)
    ax.set_xlabel('number of cells',fontsize=FontSize)
    ax.set_ylabel('relative error [%]',fontsize=FontSize)
    ax.set_title('Relative error as a function of cell count',fontsize=FontSize)
    ax.set_xlim(NN[0],NN[-1])
    ax.set_ylim(err[-1],err[0])
    for label in (ax.get_xticklabels() + ax.get_yticklabels()):
        label.set_fontsize(FontSize)
    ax.grid(which='both')
    
    plt.show()


---
## Task 2.1
---

Replace $u$, $v$, and $p$ in the Navier-Stokes equations

$$\dfrac{\partial u}{\partial x}+\dfrac{\partial v}{\partial y}=0$$

$$\rho\left(u\dfrac{\partial u}{\partial x}+v\dfrac{\partial u}{\partial y}\right)=-\dfrac{\partial p}{\partial x}+\rho g_x+\dfrac{\partial}{\partial x}\left(\mu\dfrac{\partial u}{\partial x}\right)+\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial u}{\partial y}\right)$$

$$\rho\left(u\dfrac{\partial v}{\partial x}+v\dfrac{\partial v}{\partial y}\right)=-\dfrac{\partial p}{\partial y}+\rho g_y+\dfrac{\partial}{\partial x}\left(\mu\dfrac{\partial v}{\partial x}\right)+\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial v}{\partial y}\right)$$

with

$$u=\overline{u}+u^\prime,\ v=\overline{v}+v^\prime,\ p=\overline{p}+p^\prime$$

and derive the the Reynolds-Averaged Navier-Stokes (RANS) equations. Use the fact that the time average of a fluctuation is zero. Then, use the same arguments as in Task 1.1 to show that the equations can be simplified to the following relation for our specific problem


$$0=-\dfrac{\partial \overline{p}}{\partial x}+\dfrac{\partial}{\partial y}\left(\mu\dfrac{\partial \overline{u}}{\partial y}-\rho\overline{u^\prime v^\prime}\right)$$


**Hint:** make use of the derivation available in the lecture notes for Chapter 6 ([MTF053_C06.pdf](https://courses.onlineflowcalculator.com/fluidmech/notes/MTF053_C06.pdf)).

### Answer to task 2.1

<font color="red">**present your derivations here**</font>

**Note!** derivations made uisng pen and paper or a tablet can be included as photos/images. Upload the photo or image and include as described at the top of this document.


---
## Task 2.2
---

In the task 2.2 main code below, set the number of cells to $N=1000$. Run the turbulent flow solver for 50, 100, 200, and 300 iterations and monitor the development of the solution.

1. How does the number of iterations affect the velocity profile? 

    <font color="red">**write your answer here**</font>

2. Suggest a measure of convergence for the numerical simulation and estimate the number of iterations needed to reach convergence.

    <font color="red">**write your answer here**</font>

3. When converged, the velocity profile has significantly lower velocities than the parabolic profile that was used as a starting guess. What is the reason for that? Suggest an alternative starting guess.

    <font color="red">**write your answer here**</font>

4. Calculate the Reynolds number for the turbulent flow.

    <font color="red">**write your answer here**</font>


### Turbulent flow solver
Below you find a turbulent flow solver for fully developed channel flow written in `python`.

In [6]:

# FUNCTION: turbulent_flow_solver(y,U,Niter,mu,rho,dpdx,u0,verbose)

#********************************************************
#
# NO CODE MODIFICATIONS NEEDED IN THIS NOTEBOOK SECTION
#
#********************************************************

#========================================================
# numerical calculation of a turbulent boundary layer 
# velocity profile using a finite-volume approach
#========================================================
#
#      0     1     2            N-1    N    N+1
#   ------------------- - - - -------------------
#   |     |     |     |       |     |     |     |
#   |  o  |  o  |  o  |       |  o  |  o  |  o  |
#   | G1  |     |     |       |     |     | G2  |
#   ------------------- - - - -------------------
#      ^                                  ^      
#     y=y0                              y=h/2    
#     u=u0                             du/dy=0
#
# The computational domain contains N cells ranging 
# from cell 1 to cell N. G1 and G2 are ghost cells 
# (cells outside of the computational domain used for
# boundary condition implementation).
#========================================================

def turbulent_flow_solver(y,U,Niter,mu,rho,dpdx,u0,verbose):
    
    N = len(y)-2
    
    relax =  0.5    # under relaxation

    # cell centers (excluding ghost cells): u_(1) to y_(N)
    y0=y[slice(1,N+1)]

    # right-shifted cell centers: y_(2) to y_(N+1) 
    # (right ghost cell (G2) included)    
    yp = y[slice(2,N+2)]

    # left-shifted cell centers: y_(0) to y_(N-1)
    # (left ghost cell (G1) included)  
    ym = y[slice(0,N)]
    
    # cell center velocity vector: U_(1) to U_(N)
    U0=U[slice(1,N+1)]

    # right-shifted velocity vector: U_(2) to U_(N+1)
    # (right ghost cell (G2) included) 
    Up=U[slice(2,N+2)]

    # left-shifted velocity vector: U_(0) to U_(N-1)
    # (left ghost cell (G1) included)
    Um=U[slice(0,N)]  
    
    # note! U0, Up, and Um are not copies of U but references to U, which 
    # means that the values in U0, Up, and Um will be updated when U changes

    # generate right-hand-side vector (b)
    b0 = dpdx*dy**2
    b  = b0*np.ones(N)

    # implement boundary conditions
    U[ 0]=u0
    U[-1]=U[-2]
    
    # update velocity vector iteratively until converged 
    # (increase the number of iterations if not converged) 
    
    for i in range(Niter):

        # store the velocity vector from the previous iteration
        Uold = U.copy()

        # generate matrix diagonal and off-diagonal elements

        off_diagonal_p =  (rho*kappa**2* 0.25*(yp+y0)**2*(Up-U0)/(yp-y0)+mu)
        diagonal       = -(rho*kappa**2*(0.25*(yp+y0)**2*(Up-U0)/(yp-y0)+\
                                         0.25*(y0+ym)**2*(U0-Um)/(y0-ym))+2*mu)
        off_diagonal_m =  (rho*kappa**2* 0.25*(y0+ym)**2*(U0-Um)/(y0-ym)+mu)

        # assemble a sparse matrix (A)
        A = diags([diagonal,off_diagonal_m[slice(1,N)],off_diagonal_p[slice(0,N-1)]],[0, -1, 1],format="csr")

        # update right-hand-side vector (boundary cell values)
        b[ 0] = b0 - off_diagonal_m[ 0]*u0
        b[-1] = b0 - off_diagonal_p[-1]*U0[-1]

        # calculate a new velocity vector solving the linear system AU=b
        U[slice(1,N+1)] = relax*spsolve(A,b)+(1.-relax)*Uold[slice(1,N+1)]

        # set the velocity in the right ghost cell (G2) to 
        # U_(N), which ensures that du/dy=0 at the center 
        U[-1] = U[-2]
        
        if verbose :
            # calculate max difference from previous solution
            dUmax = np.max(np.abs(U-Uold))
            print('iteration %4d of %4d, max change: %e' %(i+1,Niter,dUmax))  
    
    return U
    

### Running the turbulent flow solver
Here you define variables necessary to run the turbulent flow solver. Make sure to run the code above first since the function defined there will be used in the code below.

In [9]:

# TASK 2.2 main code

#********************************************************
#
# CODE MODIFICATION NEEDED: 
#
# 1. SPECIFY CELL COUNT
# 2. RUN THE TURBULENT FLOW SOLVER FOR THE NUMBER OF 
#    ITERATIONS SPECIFIED IN THE TASK (50, 100, 200, 300)
#    THE 50 ITERATIONS CASE IS GIVEN AS AN EXAMPLE
# 3. ADD THE RESULTS IN THE PLOT AT THE END OF THE SCRIPT
#
#********************************************************

# case-specific properties

dpdx  = -8.0   # pressure gradient

# solver settings

N     =  0     # number of cells      <= SPECIFY CELL COUNT HERE

if N > 0 :

    # we will assume that we are in the log-region and thus the 
    # lower boundary will coincide with the lower end of the 
    # log region (here assumed to be at y+=30). The velocity 
    # at y+=30 is calculated using the log law.

    yplus0     = 30
    ustar_turb = np.sqrt(-dpdx*h/(2.0*rho))
    y0         = yplus0*mu/(rho*ustar_turb)
    u0         = ustar_turb*np.log(yplus0)/kappa+B*ustar_turb

    # calculate cell size (dy) assuming equidistant grid

    dy = (0.5*h-y0)/(N+0.5)

    # generate cell center coordinate vectors

    # cell centers (including ghost cells): y_(0) to y_(N+1)
    y_turb = np.linspace(y0,0.5*h+0.5*dy,N+2)

    # initialize velocity vector (U) 
    # here a laminar solution is used as the initial condition

    U_turb = get_analytic_laminar_velocity_profile(y_turb,h,dpdx,mu)

    #********************************************************
    #
    # RUN THE TURBULENT FLOW SOLVER WITH THE SPECIFIED INPUT
    #
    #********************************************************

    # 50 ITERATIONS

    U_turb = turbulent_flow_solver(y_turb,U_turb,50,mu,rho,dpdx,u0,verbose)
    U_turb_50 = U_turb.copy()

    # <= RUN THE TURBULENT FLOW SOLVER FOR 100, 200 AND 300 ITERATIONS

    # NOTE! YOU SINCE YOU WILL SEND THE PREVIOUS SOLUTION TO THE SOLVER 
    # AS START SOLUTION, YOU SHOULD NOT SPECIFY THE TOTAL NUMBER OF ITERATIONS
    # BUT RATHER THE NUMBER OF ITERATIONS TO BE ADDED. SO IF YOU WANT TO RUN 
    # 100 ITERATIONS STARTING FROM U_turb THE PREVIOUS SOLUTION YOU SHOULD 
    # SPECIFY 50 ITERATIONS

    # set last y-coordinate to channel center
    y_turb[-1] = h/2.    

    # plot velocity profiles

    fig = plt.figure(num=1, figsize=(15, 10), dpi=80, facecolor='w', edgecolor='k')
    ax  = fig.add_subplot(111)
    ax.plot(U_turb_50,y_turb,linewidth=2,label='50 iterations')
    # <= ADD PLOTS FOR 100, 200 & 300 ITERATIONS HERE
    ax.set_xlabel('axial velocity (u [m/s])',fontsize=FontSize)
    ax.set_ylabel('wall-normal coordinate (y [m])',fontsize=FontSize)
    ax.set_title('Velocity profile - turbulent channel flow',fontsize=FontSize)
    ax.legend(fontsize=FontSize)
    for label in (ax.get_xticklabels() + ax.get_yticklabels()):
        label.set_fontsize(FontSize)
    ax.grid()
    
    plt.show()


---
## Task 2.3
---

In the provided `Python` function `turbulent_flow_solve`, there is a variable called `relax` used as follows:

`U = relax*spsolve(A,b)+(1.-relax)*Uold`

where `U` is a vector containing the velocity values in all cells, `A` is a coefficient matrix,  `b` is the right-hand side vector, `spsolve` is a `Python` function solving linear equation systems (in our case `AU=b`), and `Uold` is a vector containing the velocity values from the previous iteration. What does the `relax` variable do

### Answer to task 2.3

<font color="red">**write down your answer here**</font>


---
## Task 2.4
---

$u^+$ is a non-dimensional velocity and $y^+$ is a non-dimensional wall-normal coordinate, respectively. The definitions of $u^+$, $y^+$, and the shear velocity $u^\ast$ are repeated here for convenience

$$y^+=\dfrac{yu^\ast}{\nu}$$

$$u^+=\dfrac{\bar{u}}{u^\ast}$$

$$u^\ast\equiv\sqrt{\dfrac{\tau_w}{\rho}}$$

1. Why is it common to present the boundary layer velocity profile in terms of $y^+$ and $u^+$ rather than $y$ and $\bar{u}$?

    <font color="red">**write your answer here**</font>

2. What range of $y^+$ values corresponds to the viscous sublayer?

    <font color="red">**write your answer here**</font>

3. What range of $y^+$ values defines the log-region?

    <font color="red">**write your answer here**</font>
   
4. How does the turbulence viscosity $\mu_t$ compare to the fluid viscosity $\mu$ in the viscous sublayer and in the log-region, respectively?

    <font color="red">**write your answer here**</font>

5. How does the total shear stress vary with distance from the wall in the viscous sublayer and in the log-region, respectively?

    <font color="red">**write your answer here**</font>

6. How are the velocity profiles characterized mathematically in the viscous sublayer and in the log-region, respectively?

    <font color="red">**write your answer here**</font>



---
## Task 2.5
---

In the task 2.5 main code below, you have been provided with average velocity and corresponding wall-normal coordinates obtained from measurements in a turbulent boundary layer over a **flat plate** in a wind tunnel. 


1. Obtain an estimate of the shear velocity ($u^\ast$) from the provided data. Follow the procedure described in [MTF053_CA1.pdf](https://courses.onlineflowcalculator.com/fluidmech/docs/MTF053_CA1.pdf) and make changes to the `Python` code below where indicated.

    What $u^\ast$ value do you get?
    
    <font color="red">**write your answer here**</font>
    
2. With the estimate of $u^\ast$ from the experimental data, you can now convert the provided $\overline{u}$ and $y$ values to $u^+$ and $y^+$ values. Compare these values with the corresponding data from your numerical simulation by plotting $u^+$ as a function of $y^+$ for the experiments and the numerical simulation in the same plot (use `semilogx` instead of `plot`). 

    Compare the two profiles and comment on any differences and try to draw some conclusions about the accuracy of the numerical solution and/or the measurements based on your observations.
    
    <font color="red">**write your answers here**</font>



In [8]:

# TASK 2.5 main code

#********************************************************
#
# CODE MODIFICATIONS NEEDED: 
# 
# 1. SPECIFY y+ DEFINING THE LOWER AND UPPER END 
#    OF THE LOG-REGION
# 2. IMPLEMENT A NEWTON-RAPHSON SOLVER ACCORDING TO 
#    THE DESCRIPTION ABOVE
#
#********************************************************

#========================================================
# provided measured boundary-layer data
#========================================================

y_exp = np.array([0.00015, 0.000231, 0.0003, 0.000481, 0.0006, 0.000706, 0.000931, 0.001181, 0.001406, 0.001656, 0.001881, 0.002131, 0.002356, 0.002581, 0.002831, 0.003056, 0.003306, 0.003775, 0.00415, 0.004525, 0.0049, 0.005275, 0.00605, 0.0068, 0.0072, 0.0076, 0.0083, 0.0095, 0.01057, 0.012, 0.014, 0.016, 0.019, 0.022, 0.025, 0.03])
U_exp = np.array([3.051, 3.531, 3.917, 4.579, 4.879, 5.086, 5.385, 5.637, 5.805, 5.928, 6.05, 6.139, 6.225, 6.32, 6.424, 6.463, 6.531, 6.657, 6.753, 6.828, 6.905, 6.985, 7.148, 7.265, 7.357, 7.417, 7.52, 7.693, 7.829, 7.984, 8.233, 8.449, 8.683, 8.897, 9.034, 9.121])

#========================================================
# calculate y+ and u+ for the turbulent-channel-flow 
# simulation velocity profile
#========================================================

y_turb_defined = True

try: y_turb
except NameError: 
    y_turb_defined = False

if y_turb_defined :
    yplus_turb = y_turb*ustar_turb*rho/mu
    uplus_turb = U_turb/ustar_turb 

#========================================================
# calculate y+ and u+ from the provided experimental data
#========================================================

#--------------------------------------------------------
# step 1: estimate u* 
#--------------------------------------------------------

yplus_low  = 0 # <= SPECIFY THE y+ VALUE DEFINING THE LOWER END OF THE LOG-REGION HERE
yplus_high = 0 # <= SPECIFY THE y+ VALUE DEFINING THE UPPER END OF THE LOG-REGION HERE

ustar_exp = 1.0

if yplus_high > yplus_low :

    # go through all locations in the boundary layer until a 
    # location within the log-region is found

    for j in range(len(U_exp)):

        # calculate rough estimates of tau_w, u*, y+, and u+        
        # make an estimate of by calculating the wall shear stress as tau_w=mu*dy/du

        tau_w=mu*U_exp[j]/y_exp[j]

        # calculate y+ and u+ from tau_w

        yplus,uplus=calc_yplus_uplus(rho,mu,tau_w,y_exp[j],U_exp[j])

        # check if the rough y+ estimate is within the log-region

        if( yplus > yplus_low/3 and yplus < yplus_high ): 

            dtau_w=10.*tau_w

            while( abs(dtau_w) > 0.0001*tau_w ):

                # do a Newton-Raphson iteration

                # <= IMPLEMENT NEWTON-RAPHSON ITERATION HERE (UPDATE dtau_w)

                # update tau_w

                tau_w=tau_w+dtau_w

                # update y+, and u+ 

                yplus,uplus=calc_yplus_uplus(rho,mu,tau_w,y_exp[j],U_exp[j])

            # again, verify that the estimate of y+ is within the log region
            # if the calculated y+ is within the log region stop, if not move 
            # one step further out from the wall and try again

            if( yplus > yplus_low and yplus < yplus_high ):
                ustar_exp = np.sqrt(tau_w/rho)
                print('estimate of u*: %f m/s (found at j=%d, y+=%f)' %(ustar_exp,j,yplus) )
                break

#--------------------------------------------------------
# step 2: calculate y+ and u+ using the estimate of u*
#--------------------------------------------------------

yplus_exp = (rho*ustar_exp/mu)*y_exp
uplus_exp = U_exp/ustar_exp

#========================================================
# plot velocity profiles
#========================================================

if ustar_exp != 1.0 :

    fig = plt.figure(num=1, figsize=(15, 10), dpi=80, facecolor='w', edgecolor='k')
    ax  = fig.add_subplot(111)

    ax.semilogx(yplus_turb,uplus_turb,linewidth=2,label='numeric')
    ax.semilogx(yplus_exp,uplus_exp,linewidth=2,label='measured')
    ax.set_xlabel(r'$y^+$',fontsize=FontSize)
    ax.set_ylabel(r'$u^+$',fontsize=FontSize)
    ax.set_title('Velocity profile (non-dimensional) - turbulent channel flow',fontsize=FontSize)
    ax.legend(fontsize=FontSize)
    for label in (ax.get_xticklabels() + ax.get_yticklabels()):
        label.set_fontsize(FontSize)
    ax.grid(which='both')
    
    plt.show()
